In [ ]:
# ..... get markers from Mantri data ..... #

In [2]:
library(Seurat)
library(SingleCellExperiment)
library(dplyr)
library(MetaMarkers)

In [3]:
# load filtered counts
# smp = c('D4', 'D7-LV', 'D7-RV', 'D10-LV', 'D10-RV', 'D14-LV', 'D14-RV')
smp = c('D4', 'D7-LV', 'D7-RV')
mat = c()
for(id in 1:length(smp)){
    sc1 = Read10X_h5(paste0('chicken_heart_scRNAseq_', smp[id], '_filtered_feature_bc_matrix.h5'))
    new_barcodes = paste0(smp[id], '_', sub('\\-.*', '', colnames(sc1)))
    colnames(sc1) <- new_barcodes
    mat = cbind(mat, sc1)
}

In [8]:
# load annotation file
tab1 = read.delim('chicken_scRNAseq_metadata.csv', sep = ',')
tab1$barcode <- tab1$X
tab1$X = NULL
rownames(tab1) <- tab1$barcode
tab1 <- tab1[(tab1$orig.ident %in% smp),]
dim(tab1)
tab1[1,]

[1] 14116    18

orig.ident nCount_RNA nFeature_RNA percent.mito S.Score  
D4_AAACCCAAGCTAAACA D4         1035       576          1.256039     0.2947094
                    G2M.Score  Phase RNA_snn_res.0.5 seurat_clusters
D4_AAACCCAAGCTAAACA 0.04598864 S     3               1              
                    scanorama_snn_res.0.5 scanorama_snn_res.0.4
D4_AAACCCAAGCTAAACA 1                     0                    
                    scanorama_snn_res.0.3 scanorama_snn_res.0.25
D4_AAACCCAAGCTAAACA 1                     0                     
                    scanorama_snn_res.0.2 day ventricle celltypes.0.5   
D4_AAACCCAAGCTAAACA 0                     D4            Cardiomyocytes-1
                    barcode            
D4_AAACCCAAGCTAAACA D4_AAACCCAAGCTAAACA

In [9]:
# trim counts matrix
keepids = match(tab1$barcode, colnames(mat))
mat2 = mat[,keepids]
dim(mat2)

[1] 24356 14116

In [10]:
# create seurat object
sce = CreateSeuratObject(counts = mat2, meta.data = tab1)
sce

An object of class Seurat 
24356 features across 14116 samples within 1 assay 
Active assay: RNA (24356 features, 0 variable features)
 1 layer present: counts

In [ ]:
# normalize data + pca
sce <- NormalizeData(sce)
sce <- FindVariableFeatures(sce)
sce <- ScaleData(sce)
sce <- RunPCA(sce)
sce <- FindNeighbors(sce, dims = 1:30)
sce <- FindClusters(sce)

In [11]:
# save seurat object
saveRDS(sce, file = 'Mantri_chicken_heart.rds')

In [ ]:
# .................................................... #

In [12]:
# get SCE object
sce2 = SingleCellExperiment(list(counts = mat2), colData = DataFrame(tab1))
assay(sce2, "cpm") = convert_to_cpm(assay(sce2))

In [13]:
tab1[1,]
table(tab1$celltypes.0.5)

orig.ident nCount_RNA nFeature_RNA percent.mito S.Score  
D4_AAACCCAAGCTAAACA D4         1035       576          1.256039     0.2947094
                    G2M.Score  Phase RNA_snn_res.0.5 seurat_clusters
D4_AAACCCAAGCTAAACA 0.04598864 S     3               1              
                    scanorama_snn_res.0.5 scanorama_snn_res.0.4
D4_AAACCCAAGCTAAACA 1                     0                    
                    scanorama_snn_res.0.3 scanorama_snn_res.0.25
D4_AAACCCAAGCTAAACA 1                     0                     
                    scanorama_snn_res.0.2 day ventricle celltypes.0.5   
D4_AAACCCAAGCTAAACA 0                     D4            Cardiomyocytes-1
                    barcode            
D4_AAACCCAAGCTAAACA D4_AAACCCAAGCTAAACA


          Cardiomyocytes-1           Cardiomyocytes-2 
                      1873                       1743 
           Dendritic cells          Endocardial cells 
                        66                       1798 
      Epi-epithelial cells      Epi-mesenchymal cells 
                      1004                        464 
              Erythrocytes           Fibroblast cells 
                      1491                        348 
 Immature myocardial cells                Macrophages 
                      2554                        196 
MT-enriched cardiomyocytes                Mural cells 
                       313                         34 
         TMSB4X high cells                Valve cells 
                       268                       1829 
Vascular endothelial cells 
                       135 

In [15]:
# get cell type markers on whole data
# getting markers for sample-specific data is worse - low AUROC and fold-change

markers = compute_markers(assay(sce2, "cpm"), cell_type_labels = sce2$celltypes.0.5)
head(markers)

group cell_type        gene  fold_change auroc     log_fdr   population_size
1 all   Cardiomyocytes-1 TPM4  3.122102    0.8517201 -1202.058 1873           
2 all   Cardiomyocytes-1 MYH15 3.667237    0.8460475 -1163.582 1873           
3 all   Cardiomyocytes-1 ACTC1 3.023225    0.8459063 -1162.641 1873           
4 all   Cardiomyocytes-1 MYL2  2.813491    0.8364572 -1099.867 1873           
5 all   Cardiomyocytes-1 TNNT2 3.334993    0.8316375 -1068.537 1873           
6 all   Cardiomyocytes-1 HSPB1 2.911825    0.8285177 -1048.509 1873           
  population_fraction average_expression se_expression detection_rate
1 0.1326863            9733.350          105.44732     0.9951949     
2 0.1326863           12210.201          252.59235     0.9861185     
3 0.1326863           17342.160          222.92951     0.9994661     
4 0.1326863           15047.786          139.34152     1.0000000     
5 0.1326863            5726.419           90.04660     0.9583556     
6 0.1326863            5266.496           68.18655     0.9850507     
  fold_change_detection precision recall   
1 1.324510              0.1685353 0.9951949
2 1.402129              0.1766788 0.9861185
3 1.212354              0.1564825 0.9994661
4 1.223048              0.1576467 1.0000000
5 1.745685              0.2109035 0.9583556
6 1.547077              0.1914695 0.9850507

In [16]:
head(markers[markers$cell_type=='Fibroblast cells',])

group cell_type        gene   fold_change auroc     log_fdr   population_size
1 all   Fibroblast cells COL1A1 4.294875    0.8328024 -224.0734 348            
2 all   Fibroblast cells RPS26  1.836911    0.7755458 -153.3623 348            
3 all   Fibroblast cells COX3   1.891150    0.7680438 -145.0828 348            
4 all   Fibroblast cells ND6    2.063915    0.7672296 -144.1979 348            
5 all   Fibroblast cells COX1   1.907950    0.7652540 -142.0653 348            
6 all   Fibroblast cells ATP6   1.913939    0.7606901 -137.1925 348            
  population_fraction average_expression se_expression detection_rate
1 0.02465288           2853.530          134.3163      0.8764368     
2 0.02465288           5436.598          145.6091      0.9856322     
3 0.02465288          20458.708          431.6828      1.0000000     
4 0.02465288           8958.453          279.6025      0.9856322     
5 0.02465288          15697.860          351.9502      1.0000000     
6 0.02465288          16560.399          397.8077      1.0000000     
  fold_change_detection precision  recall   
1 3.030921              0.07131167 0.8764368
2 1.047840              0.02580305 0.9856322
3 1.158933              0.02846393 1.0000000
4 1.336639              0.03269157 0.9856322
5 1.274465              0.03121636 1.0000000
6 1.230101              0.03016121 1.0000000

In [17]:
# save marker list
export_meta_markers(markers, "Mantri_celltype_markers.csv", names(markers))